# Ejercicio 5
(Entrega obligatoria individual en repo) Genere un video en un patio o en un hall de edificio donde en un principio se vea vacío y luego aparezca una persona. Mediante los métodos de motion detection (sin usar deep learning) logre una detección de la persona cuando entra al cuadro suponiendo la utilidad para una cámara de seguridad.
Luego sobre el mismo video aplique los algoritmos de flujo denso y disperso que se mostraron en clase.
Escriba una reflexión sobre los resultados en el formato md dentro del Jupyter Notebook.

## Búsqueda de persona

### Instalación e importación librerías

In [16]:
!pip install -q mediapy

In [17]:
import cv2
import mediapy as media
import numpy as np
from google.colab.patches import cv2_imshow

### Código

In [18]:
url = 'video.mp4'
video = media.read_video(url)
media.show_video(video)

This browser does not support the video tag.


Se puede ver en el video que la persona tiene un alto contraste con el fondo, dado la posición de la luz, la persona es lo único negro del video, el resto es mayoritariamente blanco, por lo tanto, aplicando un umbral esto se podría solucionar. Sin embargo, primero voy a probar los resultados que obtengo utilizando los métodos que estan en el collab de la teoría.

#### Funcion para procesar video

In [19]:
def video_processor(filename_in, filename_out, process_func, max_time=10, **kwargs):
    # Abrir el video de entrada para lectura
    with media.VideoReader(filename_in) as r:
        # Crear un archivo de video de salida
        with media.VideoWriter(filename_out, shape=r.shape, fps=r.fps, bps=r.bps) as w:
            count = 0
            prev_image = None

            # Iterar sobre cada imagen (fotograma) del video
            for image in r:
                new_image = media.to_uint8(image)

                if prev_image is None:
                    prev_image = new_image.copy()

                processed_image = process_func(new_image, prev_image, **kwargs)

                w.add_image(processed_image)

                prev_image = new_image.copy()

                count += 1

                # Detener el proceso si se alcanza el tiempo máximo
                if count >= max_time * r.fps:
                    break

#### Función para dibujar contornos

In [20]:
def draw_contours(frame, contours, color=(0, 255, 0), thickness=2):
    # Comprobar si la imagen es en escala de grises (1 canal)
    if len(frame.shape) == 2 or frame.shape[2] == 1:
        # Convertir la imagen de escala de grises a color (3 canales)
        result_image = cv2.cvtColor(frame, cv2.COLOR_GRAY2BGR)
    else:
        # Si ya es una imagen de color, simplemente hacer una copia
        result_image = frame.copy()

    # Dibujar cada contorno en la imagen
    for contour in contours:
        # Obtener el rectángulo delimitador para cada contorno
        x, y, w, h = cv2.boundingRect(contour)
        # Dibujar el rectángulo
        cv2.rectangle(result_image, (x, y), (x + w, y + h), color, thickness)

    return result_image

#### Función de la teoría para detectar movimientos y dibujar cuadros

In [21]:
def process_img_teoria(new_image, prev_image, **kwargs):
    new_gray = cv2.cvtColor(new_image, cv2.COLOR_RGB2GRAY)
    prev_gray = cv2.cvtColor(prev_image, cv2.COLOR_RGB2GRAY)

    # Calcular la diferencia absoluta entre los fotogramas actual y anterior
    frame_diff = cv2.absdiff(new_gray, prev_gray)

    norm_diff = cv2.normalize(frame_diff, None, 0, 255, cv2.NORM_MINMAX)

    _, thresh = cv2.threshold(norm_diff, 30, 255, cv2.THRESH_BINARY)

    # Dilatar la imagen umbralizada para mejorar la detección de contornos
    kernel = np.ones((5,5),np.uint8)
    dilated = cv2.dilate(thresh, kernel, iterations = 1)

    dilated = dilated.astype(np.uint8)

    contours, _ = cv2.findContours(dilated, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)

    filtered_contours = []
    #Filtrar contornos
    for contour in contours:
      x, y, width, height = cv2.boundingRect(contour)
      if(width > 30 and height > 50): filtered_contours.append(contour)

    if kwargs.get('draw_mode', 0) == 0:
      result_image = draw_contours(new_image, filtered_contours)
    elif kwargs.get('draw_mode', 0) == 1:
      result_image = draw_contours(thresh, filtered_contours)

    return result_image


filename_in = 'video.mp4'
filename_out = 'video_diff_full.mp4'

video_processor(filename_in, filename_out, process_img_teoria,
                max_time=10, draw_mode=1)

media.show_video(media.read_video(filename_out), fps=30)

filename_out = 'video_diff_full_2.mp4'
video_processor(filename_in, filename_out, process_img_teoria,
                max_time=10, draw_mode=0)

media.show_video(media.read_video(filename_out), fps=30)

This browser does not support the video tag.


This browser does not support the video tag.


Se puede ver que no se logra un buen resultado. Voy a probar con mi propio método

#### Función propia para detectar al sujeto

In [22]:
def process_img_propia(new_image, prev_image, **kwargs):
    new_gray = cv2.cvtColor(new_image, cv2.COLOR_RGB2GRAY)

    norm_diff = cv2.normalize(new_gray, None, 0, 255, cv2.NORM_MINMAX)

    _, thresh = cv2.threshold(norm_diff, 30, 255, cv2.THRESH_BINARY_INV)

    kernel = np.ones((5,5),np.uint8)
    dilated = cv2.dilate(thresh, kernel, iterations = 1)

    dilated = dilated.astype(np.uint8)

    contours, _ = cv2.findContours(dilated, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)

    filtered_contours = []
    #Filtrar contornos
    for contour in contours:
      x, y, width, height = cv2.boundingRect(contour)
      if(width > 30 and height > 50): filtered_contours.append(contour)


    if kwargs.get('draw_mode', 0) == 0:
      result_image = draw_contours(new_image, filtered_contours)
    elif kwargs.get('draw_mode', 0) == 1:
      result_image = draw_contours(thresh, filtered_contours)

    return result_image


filename_in = 'video.mp4'
filename_out = 'video_diff_full.mp4'

video_processor(filename_in, filename_out, process_img_propia,
                max_time=10, draw_mode=1)

media.show_video(media.read_video(filename_out), fps=30)

filename_out = 'video_diff_full_2.mp4'
video_processor(filename_in, filename_out, process_img_propia,
                max_time=10, draw_mode=0)

media.show_video(media.read_video(filename_out), fps=30)

This browser does not support the video tag.


This browser does not support the video tag.


Con este método se obtienen mejores resultados

## Aplicar Optical Flow

### Sparse

In [23]:
def process_sparse_optical_flow(new_image, prev_image):
    new_gray = cv2.cvtColor(new_image, cv2.COLOR_BGR2GRAY)
    prev_gray_image = cv2.cvtColor(prev_image, cv2.COLOR_BGR2GRAY)

    if not hasattr(process_sparse_optical_flow, "shi_tomasi_done"):
        feature_params = dict(maxCorners=300, qualityLevel=0.2, minDistance=2, blockSize=7)
        process_sparse_optical_flow.prev_points = cv2.goodFeaturesToTrack(new_gray, mask=None, **feature_params)
        process_sparse_optical_flow.mask = np.zeros_like(new_image)
        process_sparse_optical_flow.shi_tomasi_done = True

    if process_sparse_optical_flow.shi_tomasi_done:
        prev_points = process_sparse_optical_flow.prev_points
        mask = process_sparse_optical_flow.mask

    lk_params = dict(winSize=(15, 15), maxLevel=2,
                     criteria=(cv2.TERM_CRITERIA_EPS | cv2.TERM_CRITERIA_COUNT, 10, 0.03))

    new_points, status, error = cv2.calcOpticalFlowPyrLK(prev_gray_image, new_gray, prev_points, None, **lk_params)
    good_old = prev_points[status == 1]
    good_new = new_points[status == 1]
    color = (0, 255, 0)  # Color para el dibujo
    for i, (new, old) in enumerate(zip(good_new, good_old)):
        a, b = new.astype(int).ravel()
        c, d = old.astype(int).ravel()
        mask = cv2.line(mask, (a, b), (c, d), color, 2)
        new_image = cv2.circle(new_image, (a, b), 3, color, -1)

    output = cv2.add(new_image, mask)
    process_sparse_optical_flow.prev_points = good_new.reshape(-1, 1, 2)
    return output

filename_in = 'video.mp4'
filename_out = 'video_sparse.mp4'

video_processor(filename_in, filename_out, process_sparse_optical_flow,
                max_time=10)

media.show_video(media.read_video(filename_out), fps=30)

This browser does not support the video tag.


## Dense


In [24]:
def process_dense_optical_flow(new_image, prev_image):
    gray = cv2.cvtColor(new_image, cv2.COLOR_BGR2GRAY)

    if not hasattr(process_dense_optical_flow, "init_done"):
        process_dense_optical_flow.prev_gray = cv2.cvtColor(new_image, cv2.COLOR_BGR2GRAY)
        process_dense_optical_flow.mask = np.zeros_like(new_image)
        process_dense_optical_flow.mask[..., 1] = 255
        process_dense_optical_flow.init_done = True

    if process_dense_optical_flow.init_done:
        prev_gray = process_dense_optical_flow.prev_gray
        mask = process_dense_optical_flow.mask

    flow = cv2.calcOpticalFlowFarneback(prev_gray, gray, None, 0.5, 3, 15, 3, 5, 1.2, 0)
    magnitude, angle = cv2.cartToPolar(flow[..., 0], flow[..., 1])
    mask[..., 0] = angle * 180 / np.pi / 2
    mask[..., 2] = cv2.normalize(magnitude, None, 0, 255, cv2.NORM_MINMAX)
    rgb = cv2.cvtColor(mask, cv2.COLOR_HSV2BGR)
    process_dense_optical_flow.prev_grayprev_gray = gray.copy()
    return rgb

filename_in = 'video.mp4'
filename_out = 'video_dense.mp4'

video_processor(filename_in, filename_out, process_dense_optical_flow,
                max_time=20)

media.show_video(media.read_video(filename_out), fps=30)

This browser does not support the video tag.


Vemos que para este video, el optical flow denso no logra detectar muy bien la figura de la persona y resulta más util el sparse

### Conclusión
Con estos ejercicios se pudo ver la dificultad que existe al momento de tratar de detectar objetos y movimientos sin la ayuda de inteligencia artificial. Es muy dificil poder escribir un código que sirva para cualquier video ya que siempre tendremos que ajustar muchísimos parámetros dependiendo del tamaño de los objetos a detectar, la calidad del video, el contraste entre el fondo y los objetos, etc.

# Ejercicio 6
Explique cuál es diferencia entre localización de objetos y clasificación de imágenes. Muestre ejemplos de ello.

### Clasificación de imágenes
Consiste en algoritmos de itenligencia artificial que clasifican objetos dentro de imágenes. Toman una imagen y predice, con cierta probabilidad, la clase a la que pertenece. No determina qué posición x e y tiene el objeto clasificado.

### Localización de objetos
Es una evolución de los modelos de clasificación de imágenes.
Identifica y localiza entidades dentro de imágenes brindando la localización (coordenadas x e y) para identificarlas mediante un bounding box.

Aunque la localización de objetos sea más avanzada que la clasificación de imagen aún se siguen utilizando modelos de clasificación de imágenes debido a su simplicidad y eficiencia.